In [1]:
import sys
sys.path.append("/home/brunoperdigao/repos/Plan-Classification-Topologic-DGL")

# Import Libraries
from topologicpy.DGL import DGL
from topologicpy.Dictionary import Dictionary
from topologicpy.Topology import Topology
from topologicpy.Vertex import Vertex
from topologicpy.Graph import Graph
from topologicpy.Plotly import Plotly
import dgl
import torch
import random
from dgl import save_graphs, load_graphs

/home/bruno_perdigao/repos/Plan-Classification-Topologic-DGL/.venv/lib/python3.12/site-packages/torchdata/datapipes/__init__.py:18: UserWarning: 
################################################################################
WARNING!
The 'datapipes', 'dataloader2' modules are deprecated and will be removed in a
future torchdata release! Please see https://github.com/pytorch/data/issues/1196
to learn more and leave feedback.
################################################################################

  deprecation_warning()


In [2]:
path = "./data2"
dataset = DGL.DatasetByCSVPath(path, numberOfGraphClasses=0,
                           nodeATTRKey='feat', edgeATTRKey='feat',
                           nodeOneHotEncode=False, nodeFeaturesCategories=[],
                           edgeOneHotEncode=False, edgeFeaturesCategories=[], addSelfLoop=False)
print(dataset)

Done saving data into cached files.
Dataset("GraphDGL", num_graphs=200, save_path=/home/bruno_perdigao/.dgl/GraphDGL)


In [3]:
train_data, val_data, test_data = dgl.data.utils.split_dataset(dataset, [0.7, 0.1, 0.2])

In [4]:
def evaluate(model, graph, features, labels, mask):
    model.eval()
    with torch.no_grad():
        logits = model(graph, features)
        logits = logits[mask]
        labels = labels[mask]
        _, indices = torch.max(logits, dim=1)
        correct = torch.sum(indices == labels)
        return correct.item() * 1.0 / len(labels)

In [ ]:
import dgl.nn as dglnn
import torch
import torch.nn as nn
import torch.nn.functional as F
import itertools




class SAGE(nn.Module):
    def __init__(self, in_feats, hid_feats, out_feats, num_layers, activation):
        super().__init__()
        self.layers = nn.ModuleList()
        self.activation = activation
        
        # Create the specified number of hidden layers
        self.layers.append(dglnn.SAGEConv(in_feats=in_feats, out_feats=hid_feats, aggregator_type='mean'))
        for _ in range(num_layers - 1):
            self.layers.append(dglnn.SAGEConv(in_feats=hid_feats, out_feats=hid_feats, aggregator_type='mean'))
        self.layers.append(dglnn.SAGEConv(in_feats=hid_feats, out_feats=out_feats, aggregator_type='mean'))

    def forward(self, graph, inputs):
        h = inputs
        for layer in self.layers[:-1]:
            h = layer(graph, h)
            h = self.activation(h)  # Apply activation function
        h = self.layers[-1](graph, h)  # Last layer without activation
        return h

# Define hyperparameter grid
num_hidden_layers = [2, 3, 4, 5]
num_units_per_layer = [8, 16, 32, 64]
activation_functions = [F.relu, F.tanh]
learning_rates = [0.01, 0.0005, 0.001, 0.0001]
batch_sizes = [16, 32, 64]

# Create a grid of hyperparameters
param_grid = list(itertools.product(num_hidden_layers, num_units_per_layer, activation_functions, learning_rates, batch_sizes))

# Iterate over all combinations of hyperparameters
for num_layers, hid_feats, activation, lr, batch_size in param_grid:
    print(f"Training with layers: {num_layers}, units per layer: {hid_feats}, activation: {activation.__name__}, learning rate: {lr}, batch size: {batch_size}")
    
    # Initialize model and optimizer
    n_features = 5
    model = SAGE(in_feats=n_features, hid_feats=hid_feats, out_feats=14, num_layers=num_layers, activation=activation)
    opt = torch.optim.Adam(model.parameters(), lr=lr)

    for epoch in range(50):  # You can adjust the number of epochs as needed
        for i, graph in enumerate(dataset.graphs):
            node_features = graph.ndata['feat']
            node_labels = graph.ndata['label']
            train_mask = graph.ndata['train_mask']
            valid_mask = graph.ndata['val_mask']
            test_mask = graph.ndata['test_mask']
            n_features = node_features.shape[1]
            n_labels = int(node_labels.max().item() + 1)

            model.train()
            # Forward propagation
            logits = model(graph, node_features)
            # Compute loss
            loss = F.cross_entropy(logits[train_mask], node_labels[train_mask])
            # Compute validation accuracy
            acc = evaluate(model, graph, node_features, node_labels, valid_mask)
            # Backward propagation
            opt.zero_grad()
            loss.backward()
            opt.step()
            print(f"Epoch {epoch}, Loss: {loss.item()}, Validation Accuracy: {acc}")

    # Optionally, you can save the model or results for each combination



Training with layers: 2, units per layer: 8, activation: relu, learning rate: 0.01, batch size: 16
Epoch 0, Loss: 16.646562576293945, Validation Accuracy: 0.3333333333333333
Epoch 0, Loss: 15.263716697692871, Validation Accuracy: 0.0
Epoch 0, Loss: 10.60661792755127, Validation Accuracy: 0.3333333333333333
Epoch 0, Loss: 10.844165802001953, Validation Accuracy: 0.0
Epoch 0, Loss: 6.993890762329102, Validation Accuracy: 0.0
Epoch 0, Loss: 9.216212272644043, Validation Accuracy: 0.3333333333333333
Epoch 0, Loss: 8.38411808013916, Validation Accuracy: 0.0
Epoch 0, Loss: 11.242566108703613, Validation Accuracy: 0.3333333333333333
Epoch 0, Loss: 8.01506519317627, Validation Accuracy: 0.0
Epoch 0, Loss: 6.71276330947876, Validation Accuracy: 0.0
Epoch 0, Loss: 3.776129722595215, Validation Accuracy: 0.0
Epoch 0, Loss: 4.150973796844482, Validation Accuracy: 0.0
Epoch 0, Loss: 4.492766380310059, Validation Accuracy: 0.25
Epoch 0, Loss: 3.7242257595062256, Validation Accuracy: 0.33333333333333